In [5]:
# by nitta
import os
is_colab = 'google.colab' in str(get_ipython())   # for Google Colab

if is_colab:
    from google.colab import drive
    drive.mount('/content/drive')
    SAVE_PATH='/content/drive/MyDrive/DeepLearning/llm_book2'
else:
    SAVE_PATH='.'

# # variable definition in 'account.py' to access HuggingFace Hub
# MyAccount = {
#     'HuggingFace': {
#         'user': 'YourUserName',
#         'token': 'YourTokenWithWritePermission'
#     },
#     'OpenAI': {
#         'api-key': 'YourOpenAI_API_Key'
# }
# }
ACCOUNT_FILE = os.path.join(SAVE_PATH, 'account.py')
%run {ACCOUNT_FILE}             # set 'MyAccount' variable

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# LangChain

<ul>
<li>
github :
<a href="https://github.com/hwchase17/langchain">
https://github.com/hwchase17/langchain
</a></li>
<li>
公式ページ:
<a href="https://python.langchain.com/en/latest/">
https://python.langchain.com/en/latest/
</a></li>
</ul>

LangChain は、さまざまなモジュールを組み合わせることで、複雑なタスクを実行するアプリケーションを作成する。
このモジュールを Chain と呼ぶ。

Agent モジュールを使うことで、ユーザの入力から回答として求められているものを推論し、必要なツールを選択して実行する(= 行動)ことで、最適な回答を導き出す。

Agent は、回答が不十分であると判断した場合は、推論と行動を繰り返して、高い精度で複雑なタスクを実行する。

# Quickstart

<ul>
<li><a href="https://python.langchain.com/docs/get_started/quickstart">
https://python.langchain.com/docs/get_started/quickstart
</a></li>
</ul>

次の方法を説明する。

<ul>
<li>LangChain, LangSmith, LangServe のセットアップ</li>
<li>コンポーネントを chaining するプロトコルをLangChain Expression Language で使用する。(このプロトコルを用いてLangChain 自体が構築されている)</li>
<li>LangChain を用いて簡単なアプリケーションを作成する</li>
<li>LangSmith を用いてアプリケーションをトレースする</li>
<li>LangServe を用いてアプリケーションを提供する</li>
</ul>



# セットアップ



In [6]:
! pip install langchain

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 807.5/807.5 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 26.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 256.9/256.9 kB 34.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.6/66.6 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.5/138.5 kB 19.2 MB/s eta 0:00:00


LangChain を用いて構築されるアプリケーションでは、LLM呼び出しを複数回呼び出す手順を含んでいる。chain や agent 内で何が起きているかを調べる最良の方法は LangSmith を使うことである。

LangSmith を使う場合は、次の環境変数を設定すること。
<pre>
export LANGCHAIN_TRACING_V2="true"
export LANGCHAIN_API_KEY="..."
</pre>

# LangChain を用いた構築

LangChain を使うと、LLMを外部のデータソースや計算に接続するアプリケーションを構築できる。
このクィックスタートでは、そのためのいくつかの方法を示す。
返答のためのプロンプト・テンプレートのみに依存する単純な LLM chain から始める。
次に、別のデータベースからデータを取得し、それをプロンプト・テンプレートに渡す chain を構築する。
それから、チャット履歴を追加して、会話検索 chain を構築する。
これにより 前の質問を記憶されているので、LLM とチャット形式で対話できる。
最後に、質問に答えるためにデータを取得する必要があるかどうかを決定するために LLM を使う agent を構築する。
大まかに説明するが、それぞれには詳細がある。
関連するリンクを貼っておくので必要ならば参照してほしい。

# LLM Chain: OpenAI

In [7]:
#
! pip install langchain-openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.4/227.4 kB 1.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.8/77.8 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 2.3 MB/s eta 0:00:00


In [8]:
import os
os.environ["OPENAI_API_KEY"] = MyAccount["OpenAI"]["api-key"]

In [9]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI()
# llm = ChatOpenAI(openai_api_key=MyAccount["OpenAI"]["api-key"])

In [10]:
llm.invoke("how can langsmith help with testing?")

AIMessage(content='Langsmith can help with testing by providing automated testing capabilities, such as unit testing and integration testing. It can also help by generating test cases based on grammar and syntax rules, and by providing tools for analyzing test coverage and identifying potential issues in the code. Additionally, Langsmith can be used to simulate various scenarios and test edge cases, helping to ensure the reliability and quality of the software being developed.')

<h4>上記回答の機械翻訳</h4>

Langsmith は、次のようなさまざまな方法でテストを支援できます。

1. さまざまなプログラミング言語で記述されたコードのテストを迅速かつ効率的に実行できる自動テスト ツールを提供します。

2. テストを実行する前にコード内の潜在的なバグやエラーを特定するコード分析機能を提供します。

3. テスト プロセスを合理化し、テストの作成と実行を容易にするテスト フレームワークとライブラリを提供します。

4. 単体テスト、統合テスト、エンドツーエンド テストなど、さまざまなテスト手法のサポートを提供します。

5. 継続的な統合および展開ツールを提供して、テスト プロセスを自動化し、コードの変更が本番環境に展開される前に徹底的にテストされるようにします。

全体として、Langsmith は包括的なテスト機能を通じてソフトウェアの品質と信頼性の向上に役立ちます。

In [11]:
# prompt template を使って回答を誘導することができる
from langchain_core.prompts import ChatPromptTemplate
prompt = ChatPromptTemplate.from_messages([
    ("system", "You are world class technical documentation writer."),
    ("user", "{input}")
])

In [12]:
# combine these into a simple LLM chain
# In python, '|' is short hand for calling the object's __or__ method.

chain = prompt | llm

In [13]:
# 上の単純な llm への質問と同じ内容を送ってみる。"techincal writer" として回答してくれるはず。
chain.invoke({"input": "how can langsmith help with testing?"})

AIMessage(content='Langsmith can help with testing in several ways:\n\n1. Automated Testing: Langsmith can be used to generate test data for automated testing scripts. By creating realistic and diverse test data sets, Langsmith can help improve the coverage and effectiveness of automated tests.\n\n2. Performance Testing: Langsmith can generate large volumes of data to simulate real-world conditions and stress test applications. This can help identify performance bottlenecks and potential issues under heavy loads.\n\n3. Security Testing: Langsmith can generate various types of data to test the security of applications, such as SQL injection attacks, cross-site scripting, and other vulnerabilities. By providing realistic test data, Langsmith can help uncover security weaknesses in applications.\n\n4. User Acceptance Testing: Langsmith can generate test data that closely resembles real user behavior, allowing testers to validate the functionality and usability of applications from an end-

<h4>上記回答の機械翻訳</h4>

Langsmith は、次のようなさまざまな方法でテストを支援できます。

1. テストの自動化: ラングスミスは、言語仕様に基づいてテスト スクリプトまたはテスト ケースを生成することにより、テスト プロセスを自動化できます。 これは、手作業の労力を軽減し、より一貫性のある包括的なテスト範囲を確保するのに役立ちます。

2. テスト データの生成: Langsmith は、言語のルールと制約に基づいて、さまざまなシナリオのテスト データの生成を支援します。 これは、さまざまなエッジケースをテストし、システムの堅牢性を確保するのに役立ちます。

3. テスト カバレッジ分析: ラングスミスは、言語仕様に基づいてテスト カバレッジを分析し、さらにテストが必要な領域についての洞察を提供します。 これは、テスト プロセス全体の品質の向上に役立ちます。

4. 回帰テスト: Langsmith は、コード変更後にテスト ケースを自動的に再実行し、回帰を特定することで、回帰テストの実行を支援します。 これは、新しい変更によって既存の機能が損なわれないようにするのに役立ちます。

5. パフォーマンス テスト: Langsmith は、言語仕様に基づいて負荷テストを生成することにより、パフォーマンス テストを支援することもできます。 これは、さまざまな負荷条件下でのシステムのパフォーマンスを評価するのに役立ちます。

全体として、Langsmith は言語分析機能を活用することで、テスト プロセスを合理化し、効率を向上させ、テストの品質を向上させることができます。

In [14]:
# ChatModel の出力は message であるが、文字列として扱うと便利な場合が多い。
# 単純な output parser を使って、message を string に変換できる。

from langchain_core.output_parsers import StrOutputParser

chain = prompt | llm | StrOutputParser()

In [15]:
chain.invoke({"input": "how can langsmith help with testing?"})

'Langsmith is a powerful tool that can greatly assist in testing by automating various aspects of the testing process. Here are some ways Langsmith can help with testing:\n\n1. Automated Test Generation: Langsmith can automatically generate test cases based on the specifications provided, saving time and effort in creating test cases manually.\n\n2. Code Analysis: Langsmith can analyze the code under test to identify potential issues such as code smells, bugs, or vulnerabilities, helping testers focus on areas that require attention.\n\n3. Test Execution: Langsmith can execute test cases automatically, providing quick feedback on the quality of the code and identifying any failures or regressions.\n\n4. Integration with Testing Frameworks: Langsmith can integrate with popular testing frameworks like JUnit, TestNG, or Selenium, making it easier to incorporate automated testing into the development process.\n\n5. Continuous Integration: Langsmith can be integrated into continuous integra

基本的な LLM chain のせってアップ方法を解説してきた。
プロンプトやモデル、出力パーサの基礎に触れたに過ぎない。
詳しく知りたい場合は
<a hrefj="https://python.langchain.com/docs/modules/model_io">
Model I/O
</a> を参照すること。

# Retrieval Chain (検索チェイン)

元の質問 "how can langsmith help with testing?" に適切に回答するために、LLMに追加の文脈を提供する必要がある。
retrieval を用いてこれを行うことができる。
retreaval は、LLMに直接渡すには多すぎるデータがあるときに、役に立つ。
最も関連した部分だけを取得して渡すには retreaver を用いる。

この手順では、関連文書を Retriever から検索して、プロンプトに渡す。
retriever は
SQL テーブル、インターネットなど、なんでも裏で使えるが、
今回はvector storeを設定してretriever として使ってみる。
詳しい説明は
<a href="https://python.langchain.com/docs/modules/data_connection/vectorstores">
Vector stores</a>
を参照のこと。

最初に、インデックスしたいデータをロードする必要がある。
そのために WebBaseLoader を使う。
これには BeautifulSoup をインストールする必要がある。

In [16]:
! pip install beautifulsoup4

In [17]:
from langchain_community.document_loaders import WebBaseLoader

loader = WebBaseLoader("https://docs.smith.langchain.com/user_guide")

docs = loader.load()

次に、これを vector store へインデックスする必要がある。
そのためには、いくつかのコンポーネント、すなわち embedding model と vectorstore が必要となる。

### OpenAI の embedding model の場合


In [18]:
# lancchain_openai パッケージをインストールしたうえで、環境変数が設定されている必要がある。
from langchain_openai import OpenAIEmbeddings

embeddings = OpenAIEmbeddings()

In [19]:
# 簡単にするためローカルな vector store である FAISS を使う。
# まず、パッケージをインストールする
! pip install faiss-gpu   # faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.5/85.5 MB 3.4 MB/s eta 0:00:00


In [20]:
# 次に、自分の index を構築する
from langchain_community.vectorstores import FAISS
from langchain_text_splitters import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter()
documents = text_splitter.split_documents(docs)
vector = FAISS.from_documents(documents, embeddings)

このデータは vectorstore 内で index 付けされたので、retrieval chain を作成できる。
この chain は入力される質問を受け取り、関連文書を検索し、元の質問と共にこれらの文書をLLM に渡し、元の質問に回答するように依頼する。



In [21]:
# 最初に、質問を受け取り、文書を検索し、回答を生成する chain を設定する。
from langchain.chains.combine_documents import create_stuff_documents_chain

prompt = ChatPromptTemplate.from_template(
    """
    Answer the following question based only on the provided context:

    <context>
    {context}
    </context>

    Question: {input}
    """ )

document_chain = create_stuff_documents_chain(llm, prompt)

In [22]:
# 必要ならば、文書に直接渡すことでこれを自分で実行することもできる。
from langchain_core.documents import Document

document_chain.invoke({
    "input": "how can langsmith help with testing?",
    "context": [Document(page_content="langsmith can let you visualize test results")]
})

'Langsmith can help with testing by allowing you to visualize test results.'

＃しかし、最初に設定した retriever から文書を得ようと思う。
このやり方では、与えられた質問に対して、retriever を用いて最も関連が深い文書を動的に選択して、それを渡すことができる。

In [23]:
from langchain.chains import create_retrieval_chain

retriever = vector.as_retriever()
retrieval_chain = create_retrieval_chain(retriever, document_chain)

In [24]:
# これで、chain を呼び出すことができるようになった。辞書を返すが、LLMからの返答では "answer" key が回答である。
response = retrieval_chain.invoke({
    "input": "how can langsmith :help with testing?"
    })

print(response["answer"])

LangSmith can help with testing by allowing developers to create datasets, run tests on LLM applications, compare different versions of applications, use a playground environment for rapid iteration and experimentation, collect feedback from users, annotate traces for evaluation, add runs to datasets for refinement, and monitor key metrics for performance analysis.


これで 基本的な retrieval chain を設定できたことになる。
より詳しい情報は
<a href="https://python.langchain.com/docs/modules/data_connection">
Retrieval
</a> を参照すること。

# Conversation Retrieval Chain (会話検索チェイン)

これまで作成してきた chain は、単一の質問に答えるだけであった。
LLM アプリケーションの主要なタイプの一つは、chat bot である。
chain を続く質問に答えられるように調整する方法について述べる。


やはり <code>create_retrieval_chain</code> 関数を使うことができるが、
2種類の変更点がある。

<ul>
<li>検索メソッドは、直近の質問に対してのみ動作するのではなく、履歴をすべて考慮する必要がある。</li>
<li>LLM chain の最後でも、すべての履歴を考慮する必要がある。</li>
</ul>

## Updating Retrieval (検索を更新する)

検索を更新するために、新しい chain を作成する。
この chain は、最新の質問を <code>input</code> に、
会話履歴を <code>chat_history</code> に受け取り、LLM を使用して
質問クエリを生成する。

In [25]:
from langchain.chains import create_history_aware_retriever
from langchain_core.prompts import MessagesPlaceholder

# 最初に、LLM に渡して検索クエリを生成させるための、プロンプトが必要となる。

prompt = ChatPromptTemplate.from_messages([
    MessagesPlaceholder(variable_name="chat_history"),
    ("user", "{input}"),
    ("user", "Given the above conversation, generate a search query to look up in order to get information relevant to the conversation")
])

retriever_chain = create_history_aware_retriever(llm, retriever, prompt)

In [26]:
# ユーザーが引き続く質問をしたインスタンスを渡して、テストする。
from langchain_core.messages import HumanMessage, AIMessage

chat_history = [
    HumanMessage(content="Can LangSmith help test my LLM applications?"),
    AIMessage(content="Yes!")
]
retriever_chain.invoke({
    "chat_history": chat_history,
    "input": "Tell me how"
})

[Document(page_content='Skip to main content\uf8ffü¶úÔ∏è\uf8ffüõ†Ô∏è LangSmith DocsLangChain Python DocsLangChain JS/TS DocsLangSmith API DocsSearchGo to AppLangSmithUser GuideSetupPricing (Coming Soon)Self-HostingTracingEvaluationMonitoringPrompt HubProxyUser GuideOn this pageLangSmith User GuideLangSmith is a platform for LLM application development, monitoring, and testing. In this guide, we‚Äôll highlight the breadth of workflows LangSmith supports and how they fit into each stage of the application development lifecycle. We hope this will inform users how to best utilize this powerful platform or give them something to consider if they‚Äôre just starting their journey.Prototyping‚ÄãPrototyping LLM applications often involves quick experimentation between prompts, model types, retrieval strategy and other parameters.\nThe ability to rapidly understand how the model is performing ‚Äî and debug where it is failing ‚Äî is incredibly important for this phase.Debugging‚ÄãWhen developing

In [27]:
# 新しい retriever を得て、検索済みの文書を記憶しながら、会話を続けるための新しい chain を生成することができる。
prompt = ChatPromptTemplate.from_messages([
    ("system", """
    Answer the user's questions based on the below context:

    {context}
    """),
    MessagesPlaceholder(variable_name="chat_history"),
    ("user", "{input}"),
])
document_chain = create_stuff_documents_chain(llm, prompt)

retrieval_chain = create_retrieval_chain(retriever_chain, document_chain)

In [28]:
# end-to-end でテストできるようになった。

chat_history = [
    HumanMessage(content="Can LangSmith help test my LLM applications?"),
    AIMessage(content="Yes!")
]
retrieval_chain.invoke({
    "chat_history": chat_history,
    "input": "Tell me how"
})

{'chat_history': [HumanMessage(content='Can LangSmith help test my LLM applications?'),
  AIMessage(content='Yes!')],
 'input': 'Tell me how',
 'context': [Document(page_content='Skip to main content\uf8ffü¶úÔ∏è\uf8ffüõ†Ô∏è LangSmith DocsLangChain Python DocsLangChain JS/TS DocsLangSmith API DocsSearchGo to AppLangSmithUser GuideSetupPricing (Coming Soon)Self-HostingTracingEvaluationMonitoringPrompt HubProxyUser GuideOn this pageLangSmith User GuideLangSmith is a platform for LLM application development, monitoring, and testing. In this guide, we‚Äôll highlight the breadth of workflows LangSmith supports and how they fit into each stage of the application development lifecycle. We hope this will inform users how to best utilize this powerful platform or give them something to consider if they‚Äôre just starting their journey.Prototyping‚ÄãPrototyping LLM applications often involves quick experimentation between prompts, model types, retrieval strategy and other parameters.\nThe ability

LangSimth でのテストに関する文書を、これが返すことがわかる。
これは、続く質問を会話履歴に結合して、LLM が新しい質問を生成したおかげである。

この新しい retriver を得たので、検索した文書を心にとめつつ、会話を続ける新しい chain を生成できる。

In [29]:
prompt = ChatPromptTemplate.from_messages([
    ("system", """
    Answer the user's questions based on the below context:

    {context}
    """),
    MessagesPlaceholder(variable_name="chat_history"),
    ("user", "{input}"),
])

document_chain = create_stuff_documents_chain(llm, prompt)

retrieval_chain = create_retrieval_chain(retriever_chain, document_chain)

In [30]:
# end-to-end でテストする
chat_history = [
    HumanMessage(content="Can LangSmith help test my LLM applications?"),
    AIMessage(content="Yes!")
]

retrieval_chain.invoke({
    "chat_history": chat_history,
    "input": "Tell me how"
})

{'chat_history': [HumanMessage(content='Can LangSmith help test my LLM applications?'),
  AIMessage(content='Yes!')],
 'input': 'Tell me how',
 'context': [Document(page_content='Skip to main content\uf8ffü¶úÔ∏è\uf8ffüõ†Ô∏è LangSmith DocsLangChain Python DocsLangChain JS/TS DocsLangSmith API DocsSearchGo to AppLangSmithUser GuideSetupPricing (Coming Soon)Self-HostingTracingEvaluationMonitoringPrompt HubProxyUser GuideOn this pageLangSmith User GuideLangSmith is a platform for LLM application development, monitoring, and testing. In this guide, we‚Äôll highlight the breadth of workflows LangSmith supports and how they fit into each stage of the application development lifecycle. We hope this will inform users how to best utilize this powerful platform or give them something to consider if they‚Äôre just starting their journey.Prototyping‚ÄãPrototyping LLM applications often involves quick experimentation between prompts, model types, retrieval strategy and other parameters.\nThe ability

一貫した回答が得られたことがわかる。retrieval chain (質問チェイン)を chat bot へと調整することができた。

# Agent

各ステップが事前にわかっている chain 例を作成してきた。
最後に作成するのは agent で、agent では LLM がどのステップを取るかを決定する。

<b>[注意] ローカルなモデルはまだ信頼性がないので、OpenAI モデルを使った agent の作り方のみを説明する。</b>

agent を構築するときにさいしょにすべきなのは、どのツールにアクセスできるかを決定することである。
この例では、agent が2つのツールにアクセスできるものとする。

<ol>
<li>たった今作成した retriever。これにより、LangSmith に関する質問に簡単に答えることができる。</li>
<li>検索ツール。これにより、最新のデータ情報が必要な質問に簡単に答えることができる。</li>
</ol>

最初に、たった今作成した retriever 用のツールをセットアップする。

In [31]:
from langchain.tools.retriever import create_retriever_tool

retriever_tool = create_retriever_tool(
    retriever,
    "langsmith_search",
    """\
    Search for information about LangSmith. \
    For any questions about LangSmith, \
    you must use this tool!\
    """,
)

使用する検索ツールは Tavily である。
<a href="https://tavily.com/">https://tavily.com/</a>

Tavily API の使用は、限定的ならば無料である。
クレジットカードの入力無しでサインアップして API キーを取得できる。

In [32]:
# 検察ツールは Tavily である。
import os
os.environ["TAVILY_API_KEY"] = MyAccount["Tavily"]["api-key"]

In [33]:
from langchain_community.tools.tavily_search import TavilySearchResults

search = TavilySearchResults()

In [34]:
tools = [retriever_tool, search]

ツールを準備したので、これらを使う agent を生成する。


In [35]:
! pip install langchainhub

In [36]:
from langchain_openai import ChatOpenAI
from langchain import hub
from langchain.agents import create_openai_functions_agent
from langchain.agents import AgentExecutor

prompt = hub.pull("hwchase17/openai-functions-agent")
llm = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
agent = create_openai_functions_agent(llm, tools, prompt)
agent_executor = AgentExecutor(agent=agent, tools=tools, verbose=True)

In [37]:
agent_executor.invoke({"input":"how can langsmith help with testing?"})



> Entering new AgentExecutor chain...

Invoking: `langsmith_search` with `{'query': 'how can LangSmith help with testing'}`


Skip to main contentü¶úÔ∏èüõ†Ô∏è LangSmith DocsLangChain Python DocsLangChain JS/TS DocsLangSmith API DocsSearchGo to AppLangSmithUser GuideSetupPricing (Coming Soon)Self-HostingTracingEvaluationMonitoringPrompt HubProxyUser GuideOn this pageLangSmith User GuideLangSmith is a platform for LLM application development, monitoring, and testing. In this guide, we‚Äôll highlight the breadth of workflows LangSmith supports and how they fit into each stage of the application development lifecycle. We hope this will inform users how to best utilize this powerful platform or give them something to consider if they‚Äôre just starting their journey.Prototyping‚ÄãPrototyping LLM applications often involves quick experimentation between prompts, model types, retrieval strategy and other parameters.
The ability to rapidly understand how the model is performing ‚Äî and deb

{'input': 'how can langsmith help with testing?',
 'output': 'LangSmith can help with testing in various ways throughout the application development lifecycle. Here are some key ways LangSmith supports testing:\n\n1. Prototyping: LangSmith allows for quick experimentation between prompts, model types, retrieval strategies, and other parameters to understand how the model is performing and debug any issues.\n\n2. Debugging: LangSmith provides clear visibility and debugging information at each step of an LLM sequence, making it easier to identify and root-cause issues when things go wrong.\n\n3. Initial Test Set: Developers can create datasets of inputs and reference outputs to run tests on their LLM applications. LangSmith makes it easy to run custom evaluations to score test results.\n\n4. Comparison View: LangSmith offers a user-friendly comparison view for test runs to track and diagnose regressions in test scores across multiple revisions of an application.\n\n5. Playground: LangSmi

In [38]:
agent_executor.invoke({"input":"what is the weather in SF?"})



> Entering new AgentExecutor chain...

Invoking: `tavily_search_results_json` with `{'query': 'weather in San Francisco'}`


[{'url': 'https://www.accuweather.com/en/us/san-francisco/94103/hourly-weather-forecast/347629', 'content': 'Get the latest hourly weather conditions and outlook for San Francisco, CA, including temperature, precipitation, wind, air quality and more. See the cloud cover, visibility and cloud ceiling for each hour until 11 PM.'}, {'url': 'https://weather.com/weather/tenday/l/San Francisco CA USCA0987:1:US', 'content': "Comfy & Cozy\nThat's Not What Was Expected\nOutside\n'No-Name Storms' In Florida\nGifts From On High\nWhat To Do For Wheezing\nSurviving The Season\nStay Safe\nAir Quality Index\nAir quality is considered satisfactory, and air pollution poses little or no risk.\n Health & Activities\nSeasonal Allergies and Pollen Count Forecast\nNo pollen detected in your area\nCold & Flu Forecast\nFlu risk is low in your area\nWe recognize our responsibility to u

{'input': 'what is the weather in SF?',
 'output': 'I found some sources where you can check the weather in San Francisco:\n\n1. [AccuWeather - Hourly Weather Forecast](https://www.accuweather.com/en/us/san-francisco/94103/hourly-weather-forecast/347629): Get the latest hourly weather conditions and outlook for San Francisco, CA, including temperature, precipitation, wind, air quality, and more.\n\n2. [The Weather Channel - 10 Day Weather Forecast](https://weather.com/weather/tenday/l/San Francisco CA USCA0987:1:US): Check the 10-day weather forecast for San Francisco, CA, including details on temperature, precipitation, and more.\n\n3. [AccuWeather - Current Weather Conditions](https://www.accuweather.com/en/us/san-francisco/94103/current-weather/347629): Get the latest weather conditions and outlook for San Francisco, CA, including temperature, humidity, wind, pressure, and cloud cover.\n\n4. [AccuWeather - Weather Forecast](https://www.accuweather.com/en/us/san-francisco/94103/weath

In [39]:
chat_history = [
    HumanMessage(
        content="Can LangSmith help test my LLM applications?"
    ),
    AIMessage(content="Yes!")
]
agent_executor.invoke({
    "chat_history": chat_history,
    "input": "Tell me how"
})



> Entering new AgentExecutor chain...

Invoking: `langsmith_search` with `{'query': 'LangSmith LLM application testing services'}`


Skip to main contentü¶úÔ∏èüõ†Ô∏è LangSmith DocsLangChain Python DocsLangChain JS/TS DocsLangSmith API DocsSearchGo to AppLangSmithUser GuideSetupPricing (Coming Soon)Self-HostingTracingEvaluationMonitoringPrompt HubProxyUser GuideOn this pageLangSmith User GuideLangSmith is a platform for LLM application development, monitoring, and testing. In this guide, we‚Äôll highlight the breadth of workflows LangSmith supports and how they fit into each stage of the application development lifecycle. We hope this will inform users how to best utilize this powerful platform or give them something to consider if they‚Äôre just starting their journey.Prototyping‚ÄãPrototyping LLM applications often involves quick experimentation between prompts, model types, retrieval strategy and other parameters.
The ability to rapidly understand how the model is performing ‚Äî 

{'chat_history': [HumanMessage(content='Can LangSmith help test my LLM applications?'),
  AIMessage(content='Yes!')],
 'input': 'Tell me how',
 'output': 'LangSmith is a platform for LLM application development, monitoring, and testing. Here are some ways LangSmith can help test your LLM applications:\n\n1. Prototyping: LangSmith supports quick experimentation between prompts, model types, retrieval strategies, and other parameters for prototyping LLM applications.\n\n2. Debugging: LangSmith provides tracing capabilities to help debug issues in LLM applications by giving clear visibility and debugging information at each step of an LLM sequence.\n\n3. Initial Test Set: Developers can create datasets of inputs and reference outputs to run tests on their LLM applications. LangSmith makes it easy to run custom evaluations to score test results.\n\n4. Comparison View: LangSmith offers a user-friendly comparison view for test runs to track and diagnose regressions in test scores across mult

基本的な agent を設定することができた。
もっと詳しい情報は
<a href="https://python.langchain.com/docs/modules/agents">
Agents
</a> を参照してほしい。

# Serving with LangServe (LangServe でサービスを提供する)

アプリケーションを構築したので、それを外部に提供する。
ここで LangServe が必要になる。
LangServe は LangChain chain を REST API として配備するのに役に立つ。

この文書はこれまで Jupyter で実行することを意図していたが、これ以降は Python ファイルを作成してコマンドラインから対話実行する。

In [40]:
! pip install "langserve[all]"

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 938.0/938.0 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.1/92.1 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.5/71.5 kB 11.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.6/60.6 kB 8.8 MB/s eta 0:00:00


## Server
略



In [41]:
!python {SAVE_PATH}/langserve_serv.py

python3: can't open file '/content/drive/MyDrive/DeepLearning/llm_book2/langserve_serv.py': [Errno 2] No such file or directory



## CLient

略